# Visualizing Wildfires 01: _No title_

De haber descubierto Altair mucho antes de empezar la tesis, creo que hubiese hecho una página de internet con visualizaciones interactivas. Sin embargo, lo descubrí algo _tarde_ pero eso no significa que no pueda replicar o re-visualizar algunas cosas.

En esta _jupyter notebook_ intentaré realizar un mapa estático y otro interactivo de los incendios forestales en todo México.

In [1]:
# Data manipulation
import numpy as np
import pandas as pd
import geopandas

# Data Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt

## Load the data

Los datos son del script [**`data_prep.py`**]()

In [2]:
# Instances (wildfire records)
gdf_wildfires_points = geopandas.read_file("./../../data/vector_conafor_wildfires_2017_points_clean_2022-03-02.geojson")
# State info
gdf_mx_states = geopandas.read_file("./../../data/vector_conafor_wildfires_2017_states_clean_2022-03-02.geojson")

## Relevant features

La información para las visualizaciones es _poca_ y es la siguiente:

In [3]:
list_relevant_vars_points = ['Latitude','Longitude','Estado', 'Duración días',
                             'Tamaño', 'Total', 'Fecha Inicio', 'ANP hectareas', 'geometry']
gdf_wildfires_points = gdf_wildfires_points[list_relevant_vars_points]

## Translate values

La publicación de las visualizaciones serán en inglés y por ello vamos a traducir tanto el nombre de las columnas asi como los valores de las categorías

In [4]:
gdf_wildfires_points = gdf_wildfires_points.rename(columns={'Estado':'State','Duración días':'DurationDays',
                       'Tamaño':'TypeSize','Total':'TotalHectares', 'Fecha Inicio':'Date',
                       'ANP hectareas':'HectaresANP'})

gdf_wildfires_points['DurationDays'] = gdf_wildfires_points['DurationDays'].astype('category')\
                                       .cat.rename_categories(['1 day','2 to 3 days','4 to 7 days','More than 7 days'])\
                                       .astype('object')

gdf_wildfires_points['TypeSize'] = gdf_wildfires_points['TypeSize'].astype('category')\
                                   .cat.rename_categories(['0 to 5 hectares', '11 to 20 hectares',
                                                           '21 to 50 hectares','51 to 100 hectares',
                                                           '6 to 10 hectares', 'More than 100 hectares'])\
                                   .astype('object')

gdf_mx_states = gdf_mx_states.rename(columns={'Estado':'State', 'ANP hectareas':'HectaresANP',
                                              'Total':'TotalHectares', 'NumIncendios':'NumWildfires' })

## Get month of the year

In [5]:
gdf_wildfires_points['Date'] = pd.to_datetime(gdf_wildfires_points['Date'])
gdf_wildfires_points['Month'] = gdf_wildfires_points['Date'].dt.month_name()#.astype('category')

## First Map: Scatter plot (Day duration + Affected Area)

***
Report $\to$ Datapane
***

In [6]:
# Base Map
base = alt.Chart(data=gdf_mx_states).mark_geoshape(fill='#FFF7EE', stroke='black', strokeWidth=0.2, opacity=0.75)

caption_p1 = alt.Chart({'values':[{}]}).mark_text(align='left', font='Georgia', fontStyle='italic', fontSize=8)\
.encode(x=alt.value(10),y=alt.value(325),text=alt.value(['Data: Comisión Nacial Forestal (CONAFOR)',
                                                         'Visualization by Isaac Arroyo (@unisaacarroyo)']))

points = alt.Chart(gdf_wildfires_points.sample(n=5000)).mark_circle(opacity=0.4, stroke='black',
                                                                    strokeWidth=0.2, strokeOpacity=0.7)\
         .encode(latitude = alt.Latitude(shorthand='Latitude'),
                 longitude = alt.Longitude(shorthand='Longitude'),
                 color = alt.Color(shorthand='DurationDays:N',
                                   #scale = alt.Scale(range=['#813405','#d45113','#f9a03f','#023047']),
                                   legend = alt.Legend(title='Duration days', orient='none', legendX=345, legendY=120)),
                 size = alt.Size(shorthand='TypeSize:O',
                                 legend = alt.Legend(title='Wildfire size', orient='none', legendX=345, legendY=5,),
                                 sort=['0 to 5 hectares', '6 to 10 hectares',
                                       '11 to 20 hectares','21 to 50 hectares',
                                       '51 to 100 hectares','More than 100 hectares'],
                                 scale = alt.Scale(range=[10,100])),
                 tooltip = [alt.Tooltip(shorthand='State', title='State'),
                            alt.Tooltip(shorthand='DurationDays', title='Duration days'),
                            alt.Tooltip(shorthand='TotalHectares', title='Affected area (ha)'),
                            alt.Tooltip(shorthand='Month', title='When?')]
                )
p1 = base + points + caption_p1
p1\
.properties(width=500, height=350,
              title=alt.TitleParams(text=['Map of wildfire records.',' Mexico, 2017'],
                                    orient="none", align='left',dx=10, dy=280,
                                    fontSize=17 
                                   )
           )\
.configure(font='Georgia')\
.configure_view(stroke=None)\
.configure_legend(fillColor = '#EEEEEE', padding= 5, cornerRadius=10,
                  labelFontSize = 10.5, titleFontSize = 12.5)

alt.LayerChart(...)

In [7]:
# Interactive Map
points_interactive = alt.Chart(gdf_wildfires_points.sample(n=5000))\
                     .mark_circle(opacity=0.4, stroke='black',strokeWidth=0.2, strokeOpacity=0.7)\
                     .encode(x = alt.X(shorthand='Longitude', scale=alt.Scale(domain=[-120,-85]), axis=alt.Axis(title='')),
                             y = alt.Y(shorthand='Latitude', scale=alt.Scale(domain=[14,34]), axis=alt.Axis(title='')),
                             color = alt.Color(shorthand='DurationDays:N',
                                               #scale = alt.Scale(range=['#813405','#d45113','#f9a03f','#023047']),
                                               legend = alt.Legend(title='Duration days', orient='none', legendX=345, legendY=120)),
                             size = alt.Size(shorthand='TypeSize:O',
                                             legend = alt.Legend(title='Wildfire size', orient='none', legendX=345, legendY=0,),
                                             sort=['0 to 5 hectares', '6 to 10 hectares','11 to 20 hectares',
                                                   '21 to 50 hectares','51 to 100 hectares','More than 100 hectares'],
                                             scale = alt.Scale(range=[10,100])),
                             tooltip = [alt.Tooltip(shorthand='State', title='State'),
                                        alt.Tooltip(shorthand='DurationDays', title='Duration days'),
                                        alt.Tooltip(shorthand='TotalHectares', title='Affected area (ha)'),
                                        alt.Tooltip(shorthand='Month', title='When?')]
                            )
p1_interactive = points_interactive + caption_p1
p1_interactive\
.properties(width=500, height=350,
              title=alt.TitleParams(text=['Interactive map of','wildfire records.','Mexico, 2017'],
                                    orient="none", align='left',dx=10, dy=255,
                                    fontSize=17))\
.configure(font='Georgia')\
.configure_view(stroke=None)\
.configure_legend(fillColor = '#EEEEEE', padding= 5, cornerRadius=10,
                  labelFontSize = 10.5, titleFontSize = 12.5)\
.configure_axis(grid=False, ticks=False, labels=False, domain=False)\
.interactive()

alt.LayerChart(...)

## Second Map: ANP and affected area (Ratio)

In [8]:
gdf_mx_states['ANP ratio'] = gdf_mx_states['HectaresANP']/gdf_mx_states['TotalHectares']

***
Report $\to$ Datapane
***

In [9]:
caption_p2 = alt.Chart({'values':[{}]}).mark_text(align='left', font='Georgia', fontStyle='italic', fontSize=8)\
.encode(x=alt.value(10),y=alt.value(325),text=alt.value(['Data: Comisión Nacial Forestal (CONAFOR)',
                                                         'Visualization by Isaac Arroyo (@unisaacarroyo)']))

choropleth = alt.Chart(data=gdf_mx_states).mark_geoshape(stroke='black', strokeWidth=0.2)\
             .encode(color=alt.Color(shorthand='ANP ratio', type='quantitative',
                                     scale=alt.Scale(scheme='lightorange'),
                                     legend = alt.Legend(title=['Ratio'],
                                                         titleAlign='left', direction='horizontal',
                                                         orient='none', legendX=265, legendY=5,
                                                         gradientThickness=20, gradientLength=220)),
                     tooltip = [alt.Tooltip(shorthand='State', title='State'),
                               alt.Tooltip(shorthand='NumWildfires', title='Number of wildfires'),
                               alt.Tooltip(shorthand='HectaresANP', title='ANP affected hectares'),
                               alt.Tooltip(shorthand='TotalHectares', title='Total affected hectares'),
                               alt.Tooltip(shorthand='ANP ratio', title = 'Radio')])

p2 = choropleth + caption_p2
p2\
.properties(width=500, height=350,
              title=alt.TitleParams(text=['Map of ANP affected',
                                          'hectares and the total',
                                          'per state. Mexico, 2017'],
                                    orient="none", align='left',dx=10, dy=255,
                                    fontSize=17))\
.configure(font='Georgia')\
.configure_view(stroke=None)\
.configure_legend(fillColor = 'transparent', padding= 5, cornerRadius=10,
                  labelFontSize = 10.5, titleFontSize = 12.5)

alt.LayerChart(...)

## Prepare data for R

In [10]:
fourth_column = gdf_wildfires_points.pop("Month")
gdf_wildfires_points.insert(4, 'Month', fourth_column)

In [11]:
fourth_column = gdf_mx_states.pop("ANP ratio")
gdf_mx_states.insert(4, "ANP ratio", fourth_column)